In [ ]:
import sys

In [ ]:
word_dict = {}
pos_dict = {None: 0}
with open("umbc.casesensitive.word_pos.1M.txt", encoding="utf8") as f:
    for line in f:
        try:
            word, pos = line.strip().split('\t')
            
            if word not in word_dict:
                word_dict[word] = len(word_dict)
                
            if pos not in pos_dict:
                pos_dict[pos] = len(pos_dict)
        
        except:
            print(line.strip(), file=sys.stderr)

i2w = {word_dict[w]: w for w in word_dict}
i2p = {pos_dict[pos]: pos for pos in pos_dict}
print(i2p)

In [ ]:
import numpy
k = 3
pos_prob = numpy.zeros((len(pos_dict),)*k, dtype=float)
word_prob = numpy.zeros((len(pos_dict),len(word_dict)), dtype=float)

prev = (0, 0)
with open("umbc.casesensitive.word_pos.1M.txt", encoding="utf8") as f:
    for line in f:
        try:
            word, pos = line.strip().split('\t')
            pos_tuple = prev + (pos_dict[pos],)
            
            word_prob[pos_dict[pos], word_dict[word]] += 1
            
            prev = pos_tuple[1:]
            pos_prob[pos_tuple] += 1
            
        except:
            print(line.strip(), file=sys.stderr)
            prev = (0, 0)
pos_prob /= pos_prob.sum(axis=k-1)[:, :, None]
word_prob /= word_prob.sum(axis=1)[:, None]

In [ ]:
pos_prob[pos_dict["DT"], pos_dict["NN"]]
print(numpy.where(word_prob[pos_dict["DT"]] > 0))

In [ ]:
def viterbi(words):
    # ["You", "talk", "the", "talk", ",", "but", "do", "you", "walk", "the", "walk", "?"]
    
    table = numpy.zeros((len(pos_dict),)*(k-1) + (len(words),), dtype=float)
    
    for i in range(len(pos_dict)):
        table[0, i, 0] = word_prob[i,word_dict[words[0]]]
    
    for t in range(1, len(words)):
        for pos1 in range(len(pos_dict)):
            for pos2 in range(len(pos_dict)):
                # (*, pos1, pos2)
                # pos2 szófajú az aktuális szó (words[i])
                maximum = 0
                for prev_pos in range(len(pos_dict)):
                    # (prev_pos, pos1, pos2)
                    x = table[prev_pos, pos1, t-1] * \
                        pos_prob[prev_pos, pos1, pos2] * \
                        word_prob[pos2, word_dict[words[t]]]
                    if x > maximum:
                        maximum = x
                table[pos1, pos2, t] = maximum
    """from a list of strings returns the optimal probability"""
    maximum = 0
    best = (0,0)
    for pos1 in range(len(pos_dict)):
        for pos2 in range(len(pos_dict)):
            if table[pos1, pos2, -1] > maximum:
                best = (pos1, pos2)
                maximum = table[pos1, pos2, -1]
    # print(table[5,:,-1])
    return best

In [ ]:
viterbi(["You", "talk", "the", "talk", ",", "but", "do", "you", "walk", "the", "walk", "?"])

In [ ]:
i2p[5], i2p[8]